In [6]:
import numpy as np
import pandas as pd
import glob
import os
import tensorflow as tf
import transformers
from transformers import TFBertForTokenClassification
from tqdm.notebook import tqdm

import sys
sys.path.append("..")
from data_preparation.data_preparation_pos import ABSATokenizer, convert_examples_to_tf_dataset, read_conll

## Zero-shot

In [2]:
import tensorflow.keras.backend as K
def ignore_acc(y_true_class, y_pred_class, class_to_ignore=0):
    y_pred_class = K.cast(K.argmax(y_pred_class, axis=-1), 'int32')
    y_true_class = K.cast(y_true_class, 'int32')
    ignore_mask = K.cast(K.not_equal(y_true_class, class_to_ignore), 'int32')
    matches = K.cast(K.equal(y_true_class, y_pred_class), 'int32') * ignore_mask
    accuracy = K.sum(matches) / K.maximum(K.sum(ignore_mask), 1)
    return accuracy

In [3]:
tagset = ["O", "_", "ADJ", "ADP", "ADV", "AUX", "CCONJ", "DET", "INTJ", "NOUN", "NUM", 
          "PART", "PRON", "PROPN", "PUNCT", "SCONJ", "SYM", "VERB", "X"]
tokenizer = ABSATokenizer.from_pretrained('bert-base-multilingual-cased')
num_labels = len(tagset)
label_map = {label: i for i, label in enumerate(tagset)}
config = transformers.BertConfig.from_pretrained('bert-base-multilingual-cased', num_labels=num_labels)
model = TFBertForTokenClassification.from_pretrained('bert-base-multilingual-cased',
                                                     config=config)
model.load_weights("../checkpoints_vi/multibert_pos_0.861_256.hdf5")
loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
model.compile(loss=loss, metrics=[ignore_acc])

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing TFBertForTokenClassification: ['nsp___cls', 'mlm___cls']
- This IS expected if you are initializing TFBertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing TFBertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of TFBertForTokenClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['dropout_37', 'classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [4]:
def load_data(path, batch_size):
    """Loads conllu file, returns a list of dictionaries (one for each sentence) and a TF dataset"""
    test_data = read_conll(glob.glob(path + "/*-test.conllu")[0])
    test_examples = [{"id": sent_id, "tokens": tokens, "tags": tags} for sent_id, tokens, tags in zip(test_data[0], 
                                                                                                      test_data[1],
                                                                                                      test_data[2])]
    test_dataset = convert_examples_to_tf_dataset(examples=test_examples, tokenizer=tokenizer, tagset=tagset, max_length=256)
    test_dataset = test_dataset.batch(batch_size)
    return test_examples, test_dataset

In [5]:
def filter_padding_tokens(test_examples, preds, label_map):
    """Filters padding tokens, labels, predictions and logits, then returns these as flattened lists"""
    filtered_preds = []
    labels = []
    tokens = []
    logits = []

    for i in range(len(test_examples)):
        example_tokens, example_labels, _ = tokenizer.subword_tokenize(test_examples[i]["tokens"], test_examples[i]["tags"])
        example_labels = [label_map[label] for label in example_labels]
        example_preds = preds[0].argmax(axis=-1)[i, :len(example_labels)]
        example_logits = preds[0][i, :len(example_labels)]
        filtered_preds.extend(example_preds)
        labels.extend(example_labels)
        tokens.extend(example_tokens)
        logits.extend(example_logits)
        
    return tokens, labels, filtered_preds, logits

In [6]:
def find_subword_locations(tokens):
    """Finds the starting and ending index of words that have been broken into subwords"""
    subword_locations = []

    for i in range(len(tokens)):
        if tokens[i].startswith("##") and not(tokens[i-1].startswith("##")):
            start = i - 1
        if not(tokens[i].startswith("##")) and tokens[i-1].startswith("##") and i != 0:
            end = i
            subword_locations.append((start, end))
            
    return subword_locations

In [7]:
def reconstruct_subwords(subword_locations, tokens, labels, filtered_preds, logits):
    """Assemble subwords back into the original word in the global lists of tokens, labels and predictions,
    and select a predicted tag"""
    new_tokens = []
    new_preds = []
    new_labels = []
    prev_end = 0

    for start, end in subword_locations:
        if len(set(filtered_preds[start:end])) > 1:
            # Subword predictions do not all agree
            temp = np.array([(M.max(), M.argmax()) for M in logits[start:end]])
            prediction = temp[temp[:,0].argmax(), 1]
        else:
            prediction = filtered_preds[start]
        new_preds += filtered_preds[prev_end:start] + [prediction]
        token = "".join(tokens[start:end]).replace("##", "")
        new_tokens += tokens[prev_end:start] + [token]
        new_labels += labels[prev_end:start] + [labels[start]]
        prev_end = end

    # Last subword onwards
    new_preds += filtered_preds[prev_end:]
    new_tokens += tokens[prev_end:]
    new_labels += labels[prev_end:]
    
    return new_tokens, new_labels, new_preds

In [8]:
data_dir = "../data/ud/"
pos_eval = {}
for directory in tqdm(os.listdir(data_dir)):
    path = os.path.join(data_dir, directory)
    batch_size = 256 # Doesn't really matter here
    test_examples, test_dataset = load_data(path, batch_size)
    preds = model.predict(test_dataset, steps=np.ceil(len(test_examples) / batch_size))
    tokens, labels, filtered_preds, logits = filter_padding_tokens(test_examples, preds, label_map)
    subword_locations = find_subword_locations(tokens)
    new_tokens, new_labels, new_preds = reconstruct_subwords(subword_locations, tokens, labels, filtered_preds, logits)
    pos_eval[directory] = (np.array(new_labels) == np.array(new_preds)).mean()

In [9]:
pos_eval  

{'ar': 0.592356994843622,
 'bg': 0.6243322309844823,
 'en': 0.5568952524491334,
 'eu': 0.5540329859686551,
 'fi': 0.5671528698617162,
 'he': 0.4644249190724714,
 'hr': 0.575886232481451,
 'ja': 0.44999438349496385,
 'ko': 0.5300289435600579,
 'ru': 0.6244252725112363,
 'sl': 0.5942585201105312,
 'th': 0.5106373449187083,
 'tr': 0.508383129314846,
 'vi': 0.8762649173005792,
 'zh': 0.5116974083586271}

In [10]:
{k: str(round(v * 100, 2)) + "%" for k, v in sorted(pos_eval.items(), key=lambda item: item[1], reverse=True)}

{'vi': '87.63%',
 'ru': '62.44%',
 'bg': '62.43%',
 'sl': '59.43%',
 'ar': '59.24%',
 'hr': '57.59%',
 'fi': '56.72%',
 'en': '55.69%',
 'eu': '55.4%',
 'ko': '53.0%',
 'zh': '51.17%',
 'th': '51.06%',
 'tr': '50.84%',
 'he': '46.44%',
 'ja': '45.0%'}

Load results excel

In [11]:
results_path = "../results/results_pos.xlsx"

if os.path.isfile(results_path):
    results = pd.read_excel(results_path, sheet_name=None)
else:
    results = {}

Check if the sheet already exists

In [12]:
sheet = "results_pos_vi"

if sheet in results:
    raise Exception("Sheet already exists and would be overwritten, aborting")
else:
    results[sheet] = pd.DataFrame({"Language": list(pos_eval.keys()), "Test_acc": list(pos_eval.values())})

Save all sheets into excel file

In [13]:
with pd.ExcelWriter("../results/results_pos.xlsx") as writer:
    for sheet_name, df in results.items():
        df.to_excel(writer, index=False, sheet_name=sheet_name)

## Example

In [39]:
test_data = read_conll("../data/ud/fi/fi_pud-ud-test.conllu")
test_examples = [{"id": sent_id, "tokens": tokens, "tags": tags} for sent_id, tokens, tags in zip(test_data[0], 
                                                                                                  test_data[1],
                                                                                                  test_data[2])]

In [58]:
# All languages
path = "../data/ud/"
test_examples = []

for lang in os.listdir(path):
    test_data = read_conll(glob.glob(path + lang + "/*-test.conllu")[0])
    temp = [{"id": sent_id, "tokens": tokens, "tags": tags} for sent_id, tokens, tags in zip(test_data[0], 
                                                                                                  test_data[1],
                                                                                                  test_data[2])]
    test_examples.extend(temp)

In [60]:
batch_size = 256
test_dataset = convert_examples_to_tf_dataset(examples=test_examples, tokenizer=tokenizer, tagset=tagset, max_length=256)
test_dataset = test_dataset.batch(batch_size)

In [64]:
example_batch = test_dataset.as_numpy_iterator().next()

for token, label in zip(example_batch[0]["input_ids"][0], example_batch[1][0]):
    if token == 0:
        break
    print("{:<25}{:<20}".format(tokenizer.decode(int(token)), tagset[label]))

ك ت ب                    VERB                
# # ت                    VERB                
ك                        PROPN               
# # و ر ي                PROPN               
ش                        PROPN               
# # و ل                  PROPN               
# # م ا ن                PROPN               
,                        PUNCT               
ا ل                      NOUN                
# # م س ا ع د ة          NOUN                
ا ل خ ا ص ة              ADJ                 
ل                        ADP                 
أ و                      PROPN               
# # ب ا                  PROPN               
# # م ا                  PROPN               
ف ي                      ADP                 
ت                        NOUN                
# # د و                  NOUN                
# # ي ن ة                NOUN                
ن ش ر                    VERB                
# # ت                    VERB                
ه ا                      PRON     

In [65]:
model.evaluate(test_dataset)

60/60 [==============================] - 263s 4s/step - loss: 0.2904 - ignore_acc: 0.6831


[0.2904379665851593, 0.6831367015838623]

In [66]:
preds = model.predict(test_dataset, steps=np.ceil(len(test_examples) / batch_size), verbose=1)

60/60 [==============================] - 268s 4s/step


In [67]:
filtered_preds = []
labels = []
tokens = []
logits = []

for i in range(len(test_examples)):
    example_tokens, example_labels, _ = tokenizer.subword_tokenize(test_examples[i]["tokens"], test_examples[i]["tags"])
    example_labels = [label_map[label] for label in example_labels]
    example_preds = preds[0].argmax(axis=-1)[i, :len(example_labels)]
    example_logits = preds[0][i, :len(example_labels)]
    filtered_preds.extend(example_preds)
    labels.extend(example_labels)
    tokens.extend(example_tokens)
    logits.extend(example_logits)

In [68]:
(np.array(labels) == np.array(filtered_preds)).mean()

0.6518227627224638

In [46]:
flattened = []
iterator = test_dataset.as_numpy_iterator()
accuracies = []
temp_preds = filtered_preds.copy()

for batch in iterator:
    batch_labels = batch[1][batch[1] != 0]
    flattened.extend(batch_labels)
    accuracies.append((np.array(batch[1][batch[1] != 0]) == np.array(temp_preds[:len(batch_labels)])).mean())
    temp_preds = temp_preds[len(batch_labels):]

In [47]:
np.mean(accuracies)

0.8352089574000712

In [48]:
(np.array(labels) == np.array(flattened)).mean()

1.0

In [69]:
start = None
end = None
subword_locations = []

for i in range(len(tokens)):
    if tokens[i].startswith("##") and not(tokens[i-1].startswith("##")):
        start = i - 1
    if not(tokens[i].startswith("##")) and tokens[i-1].startswith("##"):
        end = i
        subword_locations.append((start, end))

In [70]:
truths = []
final_most_voted = []
final_avg = []
final_first = []
final_random = []
final_max_prob = []
final_random_equi = []

for start, end in subword_locations:
    if len(set(filtered_preds[start:end])) > 1:
        print(start, end)
        print("Tokens:", tokens[start:end])
        print("Predictions:", filtered_preds[start:end])
        print("Truth:", labels[start])
        truths.append(labels[start])
        
        most_voted = max(set(filtered_preds[start:end]), key=filtered_preds[start:end].count)
        final_most_voted.append(most_voted)
        avg = sum(logits[start:end]).argmax()
        final_avg.append(avg)
        final_first.append(filtered_preds[start])
        final_random.append(np.random.choice(filtered_preds[start:end]))
        temp = np.array([(M.max(), M.argmax()) for M in logits[start:end]])
        final_max_prob.append(temp[temp[:,0].argmax(), 1])
        final_random_equi.append(np.random.choice(list(set(filtered_preds[start:end]))))

8 10
Tokens: ['ال', '##مساعدة']
Predictions: [7, 9]
Truth: 9
Final prediction: 9 

23 26
Tokens: ['ال', '##إ', '##ثنين']
Predictions: [7, 9, 10]
Truth: 13
Final prediction: 9 

32 36
Tokens: ['ال', '##ان', '##ت', '##قال']
Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

50 54
Tokens: ['ال', '##ان', '##ت', '##قال']
Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

58 61
Tokens: ['ل', '##سل', '##طة']
Predictions: [3, 9, 9]
Truth: 9
Final prediction: 9 

70 73
Tokens: ['ال', '##نس', '##بة']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

82 86
Tokens: ['ال', '##ان', '##ت', '##قال']
Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

107 110
Tokens: ['ال', '##شي', '##ء']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

112 115
Tokens: ['ب', '##عيد', '##اً']
Predictions: [4, 2, 4]
Truth: 2
Final prediction: 4 

124 126
Tokens: ['ال', '##حد']
Predictions: [7, 9]
Truth: 9
Final prediction: 9 

127 130
Tokens: ['ال', '##ه', '##جرة']
Predictions: [7, 9, 9]
Truth: 

3730 3733
Tokens: ['ن', '##حت', '##اج']
Predictions: [5, 17, 17]
Truth: 17
Final prediction: 17 

3758 3761
Tokens: ['ال', '##حمل', '##ة']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

3772 3774
Tokens: ['ي', '##قابل']
Predictions: [12, 17]
Truth: 17
Final prediction: 17 

3774 3776
Tokens: ['ال', '##طلاب']
Predictions: [7, 9]
Truth: 9
Final prediction: 9 

3797 3799
Tokens: ['ت', '##قول']
Predictions: [5, 17]
Truth: 17
Final prediction: 17 

3800 3803
Tokens: ['ال', '##سل', '##وى']
Predictions: [7, 13, 13]
Truth: 9
Final prediction: 13 

3804 3806
Tokens: ['ت', '##أتي']
Predictions: [5, 17]
Truth: 17
Final prediction: 17 

3842 3845
Tokens: ['ال', '##نس', '##بة']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

3849 3854
Tokens: ['ال', '##مت', '##أ', '##لم', '##ين']
Predictions: [7, 9, 9, 9, 9]
Truth: 9
Final prediction: 9 

3863 3866
Tokens: ['ي', '##مل', '##ك']
Predictions: [5, 17, 17]
Truth: 17
Final prediction: 17 

3866 3870
Tokens: ['ال', '##أ', '##طب', '##اء']
Pred

Tokens: ['ن', '##ن', '##حي']
Predictions: [5, 17, 17]
Truth: 17
Final prediction: 17 

7212 7214
Tokens: ['ن', '##ا']
Predictions: [10, 11]
Truth: 12
Final prediction: 10 

7217 7219
Tokens: ['ت', '##تضمن']
Predictions: [12, 17]
Truth: 17
Final prediction: 17 

7223 7226
Tokens: ['غ', '##راب', '##ة']
Predictions: [2, 9, 9]
Truth: 9
Final prediction: 9 

7227 7230
Tokens: ['ال', '##س', '##فير']
Predictions: [7, 13, 13]
Truth: 13
Final prediction: 13 

7235 7240
Tokens: ['ال', '##مس', '##تش', '##في', '##ات']
Predictions: [7, 13, 13, 13, 13]
Truth: 13
Final prediction: 13 

7254 7257
Tokens: ['ل', '##أ', '##عمال']
Predictions: [3, 9, 13]
Truth: 13
Final prediction: 9 

7259 7261
Tokens: ['ن', '##ي']
Predictions: [8, 5]
Truth: 12
Final prediction: 8 

7306 7308
Tokens: ['ن', '##ا']
Predictions: [12, 8]
Truth: 12
Final prediction: 8 

7309 7311
Tokens: ['ن', '##سمح']
Predictions: [5, 17]
Truth: 17
Final prediction: 17 

7312 7315
Tokens: ['ل', '##ر', '##ئاسة']
Predictions: [3, 13, 13]
Truth

Final prediction: 9 

10896 10898
Tokens: ['ي', '##ألف']
Predictions: [5, 17]
Truth: 17
Final prediction: 17 

10899 10901
Tokens: ['ال', '##بشر']
Predictions: [7, 9]
Truth: 9
Final prediction: 9 

10907 10909
Tokens: ['عامل', '##ت']
Predictions: [17, 13]
Truth: 9
Final prediction: 17 

10911 10913
Tokens: ['فيلم', '##ٍ']
Predictions: [9, 11]
Truth: 9
Final prediction: 9 

10921 10924
Tokens: ['ك', '##وت', '##ون']
Predictions: [9, 9, 13]
Truth: 13
Final prediction: 9 

10924 10927
Tokens: ['ال', '##شر', '##يرة']
Predictions: [7, 2, 2]
Truth: 2
Final prediction: 2 

10931 10933
Tokens: ['نوع', '##ٍ']
Predictions: [9, 16]
Truth: 9
Final prediction: 16 

10934 10937
Tokens: ['ال', '##رغ', '##بة']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

10939 10941
Tokens: ['ال', '##قتل']
Predictions: [7, 9]
Truth: 9
Final prediction: 9 

10954 10957
Tokens: ['ال', '##قر', '##يبة']
Predictions: [7, 2, 2]
Truth: 2
Final prediction: 2 

10966 10968
Tokens: ['مهم', '##اً']
Predictions: [2, 4]
Tr

Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

14896 14899
Tokens: ['ال', '##سا', '##حل']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

14899 14901
Tokens: ['مشابه', '##ٌ']
Predictions: [2, 11]
Truth: 2
Final prediction: 2 

14904 14908
Tokens: ['ال', '##ص', '##حر', '##اء']
Predictions: [13, 9, 9, 9]
Truth: 13
Final prediction: 9 

14918 14920
Tokens: ['شكل', '##ٍ']
Predictions: [9, 11]
Truth: 9
Final prediction: 9 

14937 14941
Tokens: ['ال', '##م', '##جا', '##عة']
Predictions: [7, 13, 13, 13]
Truth: 9
Final prediction: 13 

14951 14955
Tokens: ['ال', '##ح', '##ضا', '##رات']
Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

14969 14971
Tokens: ['شكل', '##ٍ']
Predictions: [9, 11]
Truth: 9
Final prediction: 9 

14986 14990
Tokens: ['ال', '##است', '##عم', '##ار']
Predictions: [7, 9, 9, 9]
Truth: 9
Final prediction: 9 

14991 14994
Tokens: ['ال', '##حر', '##وب']
Predictions: [7, 9, 9]
Truth: 9
Final prediction: 9 

14995 14998
Tokens: ['ال', '##إ', '##ضافة']
Predi

...

507138 507140
Tokens: ['基', '##督']
Predictions: [9, 13]
Truth: 9
Final prediction: 9 

507140 507142
Tokens: ['教', '##堂']
Predictions: [9, 0]
Truth: 9
Final prediction: 0 

507142 507144
Tokens: ['通', '##常']
Predictions: [2, 9]
Truth: 4
Final prediction: 9 

507147 507149
Tokens: ['主', '##日']
Predictions: [13, 9]
Truth: 9
Final prediction: 9 

507156 507158
Tokens: ['取', '##代']
Predictions: [17, 18]
Truth: 17
Final prediction: 17 

507162 507166
Tokens: ['阿', '##爾', '##卑', '##斯']
Predictions: [18, 18, 18, 14]
Truth: 13
Final prediction: 18 

507166 507168
Tokens: ['山', '##脈']
Predictions: [9, 18]
Truth: 9
Final prediction: 9 

507179 507182
Tokens: ['飲', '##用', '##水']
Predictions: [9, 9, 18]
Truth: 17
Final prediction: 9 

507183 507186
Tokens: ['灌', '##溉', '##水']
Predictions: [9, 9, 14]
Truth: 17
Final prediction: 9 

507189 507191
Tokens: ['發', '##電']
Predictions: [17, 0]
Truth: 17
Final prediction: 0 

507201 507203
Tokens: ['佔', '##據']
Predictions: [17, 2]
Truth: 17
Final predictio

511160 511162
Tokens: ['湖', '##區']
Predictions: [9, 13]
Truth: 9
Final prediction: 9 

511164 511166
Tokens: ['深', '##深']
Predictions: [2, 0]
Truth: 4
Final prediction: 0 

511166 511168
Tokens: ['打', '##動']
Predictions: [9, 0]
Truth: 17
Final prediction: 0 

511169 511171
Tokens: ['以', '##至']
Predictions: [18, 0]
Truth: 17
Final prediction: 0 

511172 511174
Tokens: ['他', '##們']
Predictions: [12, 0]
Truth: 12
Final prediction: 0 

511175 511177
Tokens: ['第', '##一']
Predictions: [2, 10]
Truth: 2
Final prediction: 2 

511178 511180
Tokens: ['孩', '##子']
Predictions: [9, 0]
Truth: 9
Final prediction: 0 

511196 511198
Tokens: ['那', '##兒']
Predictions: [7, 2]
Truth: 12
Final prediction: 2 

511213 511215
Tokens: ['一', '##同']
Predictions: [10, 4]
Truth: 4
Final prediction: 10 

511218 511222
Tokens: ['佛', '##羅', '##倫', '##薩']
Predictions: [9, 9, 9, 14]
Truth: 13
Final prediction: 9 

511222 511225
Tokens: ['葛', '##拉', '##德']
Predictions: [13, 13, 14]
Truth: 13
Final prediction: 13 

511228 

Predictions: [13, 9]
Truth: 9
Final prediction: 9 

515051 515053
Tokens: ['未', '##能']
Predictions: [5, 2]
Truth: 5
Final prediction: 2 

515075 515077
Tokens: ['真', '##的']
Predictions: [8, 14]
Truth: 4
Final prediction: 8 

515077 515079
Tokens: ['很', '##愛']
Predictions: [4, 0]
Truth: 17
Final prediction: 0 

515094 515096
Tokens: ['單', '##曲']
Predictions: [2, 9]
Truth: 9
Final prediction: 9 

515109 515111
Tokens: ['已', '##經']
Predictions: [5, 17]
Truth: 4
Final prediction: 17 

515117 515119
Tokens: ['故', '##鄉']
Predictions: [2, 14]
Truth: 9
Final prediction: 2 

515123 515125
Tokens: ['到', '##達']
Predictions: [3, 0]
Truth: 17
Final prediction: 0 

515136 515138
Tokens: ['回', '##到']
Predictions: [17, 13]
Truth: 17
Final prediction: 17 

515138 515141
Tokens: ['洛', '##杉', '##磯']
Predictions: [13, 13, 0]
Truth: 13
Final prediction: 13 

515141 515143
Tokens: ['定', '##居']
Predictions: [9, 13]
Truth: 17
Final prediction: 9 

515144 515148
Tokens: ['一', '##心', '##一', '##意']
Predictions: 

519661 519663
Tokens: ['很', '##大']
Predictions: [4, 2]
Truth: 2
Final prediction: 2 

519663 519665
Tokens: ['改', '##進']
Predictions: [9, 0]
Truth: 17
Final prediction: 0 

519669 519672
Tokens: ['伊', '##斯', '##蘭']
Predictions: [8, 18, 13]
Truth: 13
Final prediction: 8 

519699 519701
Tokens: ['需', '##要']
Predictions: [17, 0]
Truth: 17
Final prediction: 0 

519704 519706
Tokens: ['多', '##數']
Predictions: [2, 9]
Truth: 9
Final prediction: 9 

519707 519709
Tokens: ['第', '##三']
Predictions: [9, 10]
Truth: 2
Final prediction: 9 

519775 519777
Tokens: ['發', '##展']
Predictions: [17, 9]
Truth: 9
Final prediction: 17 

519807 519811
Tokens: ['尼', '##古', '##拉', '##斯']
Predictions: [13, 13, 13, 14]
Truth: 13
Final prediction: 13 

519828 519832
Tokens: ['前', '##司', '##法', '##部']
Predictions: [4, 14, 14, 14]
Truth: 9
Final prediction: 14 

519848 519851
Tokens: ['法', '##西', '##斯']
Predictions: [9, 9, 18]
Truth: 13
Final prediction: 9 

519867 519869
Tokens: ['暴', '##徒']
Predictions: [9, 0]
Trut

Final prediction: 0 

523490 523492
Tokens: ['為', '##了']
Predictions: [5, 11]
Truth: 3
Final prediction: 11 

523492 523494
Tokens: ['參', '##加']
Predictions: [17, 9]
Truth: 17
Final prediction: 17 

523507 523509
Tokens: ['不', '##得']
Predictions: [11, 5]
Truth: 5
Final prediction: 11 

523510 523512
Tokens: ['離', '##開']
Predictions: [17, 0]
Truth: 17
Final prediction: 0 

523517 523519
Tokens: ['公', '##元']
Predictions: [10, 13]
Truth: 9
Final prediction: 10 

523532 523534
Tokens: ['之', '##後']
Predictions: [3, 9]
Truth: 3
Final prediction: 9 

523537 523539
Tokens: ['逐', '##漸']
Predictions: [17, 0]
Truth: 4
Final prediction: 0 

523544 523548
Tokens: ['嶄', '##露', '##頭', '##角']
Predictions: [2, 2, 18, 14]
Truth: 17
Final prediction: 2 

523551 523553
Tokens: ['已', '##經']
Predictions: [5, 0]
Truth: 4
Final prediction: 0 

523553 523555
Tokens: ['衰', '##落']
Predictions: [17, 13]
Truth: 17
Final prediction: 17 

523577 523580
Tokens: ['字', '##母', '##表']
Predictions: [13, 13, 14]
Truth: 9
F

In [71]:
print("Most voted:", (np.array(truths) == np.array(final_most_voted)).mean())
print("Logit average:", (np.array(truths) == np.array(final_avg)).mean())
print("Always first:", (np.array(truths) == np.array(final_first)).mean())
print("Random choice:", (np.array(truths) == np.array(final_random)).mean())
print("Highest probability:", (np.array(truths) == np.array(final_max_prob)).mean())
print("Equiprobable random:", (np.array(truths) == np.array(final_random_equi)).mean())

Most voted: 0.4800012373557707
Logit average: 0.490828100349553
Always first: 0.4210721687753271
Random choice: 0.364927150678999
Highest probability: 0.49760262319423393
Equiprobable random: 0.32393974077396603


In [72]:
new_tokens = []
new_preds = []
new_labels = []
prev_end = 0

for start, end in subword_locations:
    if len(set(filtered_preds[start:end])) > 1:
        # Subword predictions do not all agree
        prediction = sum(logits[start:end]).argmax()
    else:
        prediction = filtered_preds[start]
    new_preds += filtered_preds[prev_end:start] + [prediction]
    token = "".join(tokens[start:end]).replace("##", "")
    new_tokens += tokens[prev_end:start] + [token]
    new_labels += labels[prev_end:start] + [labels[start]]
    prev_end = end
    
# Last subword onwards
new_preds += filtered_preds[prev_end:]
new_tokens += tokens[prev_end:]
new_labels += labels[prev_end:]

In [73]:
for token, label in zip(new_tokens[:20], new_labels[:20]):
    print(token, tagset[label])

كتبت VERB
كوري PROPN
شولمان PROPN
, PUNCT
المساعدة NOUN
الخاصة ADJ
ل ADP
أوباما PROPN
في ADP
تدوينة NOUN
نشرت VERB
ها PRON
يوم ADV
الإثنين PROPN
: PUNCT
" PUNCT
فيما ADP
الكثير NOUN
من ADP
عمليات NOUN


In [74]:
for token, label in zip(tokens[:30], labels[:30]):
    print(token, tagset[label])

كتب VERB
##ت VERB
ك PROPN
##وري PROPN
ش PROPN
##ول PROPN
##مان PROPN
, PUNCT
ال NOUN
##مساعدة NOUN
الخاصة ADJ
ل ADP
أو PROPN
##با PROPN
##ما PROPN
في ADP
ت NOUN
##دو NOUN
##ينة NOUN
نشر VERB
##ت VERB
ها PRON
يوم ADV
ال PROPN
##إ PROPN
##ثنين PROPN
: PUNCT
" PUNCT
فيما ADP
الكثير NOUN


In [75]:
(np.array(new_labels) == np.array(new_preds)).mean()

0.6867996536918918

## Old

In [3]:
#lang_path = os.path.join("../data/ud/", "ar")
#pos = open(glob.glob(lang_path + "/*-test.conllu")[0], "r", encoding="utf-8").read()
pos = open("../es_pud-ud-test.conllu", "r", encoding="utf-8").read()[1:]
test_sentences = parse(pos)
test_dataset = convert_examples_to_tf_dataset(examples=test_sentences, tokenizer=tokenizer, tagset=tagset, max_length=512)
test_dataset = test_dataset.shuffle(10000).batch(32).repeat(1)

In [25]:
model.evaluate(test_dataset)

32/32 [==============================] - 37s 1s/step - loss: 0.0157 - sparse_categorical_accuracy: 0.9976


[0.015721691772341728, 0.9975742101669312]

In [33]:
pos_example = """1	Aunque	_	ADP	IN	_	3	mark	_	_
2	no	_	ADV	RB	Polarity=Neg	3	advmod	_	_
3	haya	haber	VERB	VBC	Aspect=Imp|Mood=Sub|Number=Sing|Person=3|Tense=Pres|VerbForm=Fin|Voice=Act	23	advcl	_	_
4	precedentes	_	NOUN	NN	Gender=Masc|Number=Plur	3	obj	_	_
5	para	_	ADP	IN	_	8	case	_	_
6	la	el	DET	DT	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	8	det	_	_
7	mayor	_	ADJ	JJR	Degree=Cmp|Gender=Fem|Number=Sing	8	amod	_	_
8	parte	_	NOUN	NN	Gender=Fem|Number=Sing	3	obl	_	_
9	de	_	ADP	IN	_	11	case	_	_
10	la	el	DET	DT	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	11	det	_	_
11	transición	_	NOUN	NN	Gender=Fem|Number=Sing	8	nmod	_	_
12	digital	_	ADJ	JJ	Gender=Fem|Number=Sing	11	amod	_	_
13	en	_	ADP	IN	_	14	case	_	_
14	Estados	_	NOUN	NN	Gender=Masc|Number=Plur	3	obl	_	Proper=True
15	Unidos	_	ADJ	JJ	Gender=Masc|Number=Plur	14	amod	_	SpaceAfter=No|Proper=True
16	,	_	PUNCT	,	_	3	punct	_	_
17	la	el	DET	DT	Definite=Def|Gender=Fem|Number=Sing|PronType=Art	18	det	_	_
18	transición	_	NOUN	NN	Gender=Fem|Number=Sing	23	nsubj	_	_
19	de	_	ADP	IN	_	20	case	_	_
20	poder	_	NOUN	NN	Gender=Masc|Number=Sing	18	nmod	_	_
21	pacífica	_	ADJ	JJ	Gender=Fem|Number=Sing	18	amod	_	_
22	es	_	AUX	VBC	Aspect=Imp|Mood=Ind|Number=Sing|Person=3|Tense=Pres|VerbForm=Fin|Voice=Act	23	cop	_	_
23	habitual	_	ADJ	JJ	Gender=Fem|Number=Sing	0	root	_	SpaceAfter=No
24	,	_	PUNCT	,	_	25	punct	_	_
25	escribió	_	VERB	VBC	Aspect=Perf|Mood=Ind|Number=Sing|Person=3|Tense=Past|VerbForm=Fin|Voice=Act	23	parataxis	_	_
26	el	el	DET	DT	Definite=Def|Gender=Masc|Number=Sing|PronType=Art	27	det	_	_
27	lunes	_	NOUN	NN	Gender=Masc|Number=Sing	25	obl:tmod	_	_
28	en	_	ADP	IN	_	30	case	_	_
29	una	uno	DET	DT	Definite=Ind|Gender=Fem|Number=Sing|PronType=Art	30	det	_	_
30	entrada	_	NOUN	NN	Gender=Fem|Number=Sing	25	obl	_	_
31	de	_	ADP	IN	_	32	case	_	_
32	blog	_	NOUN	NN	Gender=Masc|Number=Sing	30	nmod	_	_
33	Kori	_	PROPN	NNP	Gender=Fem|Number=Sing	25	nsubj	_	_
34	Schulman	_	PROPN	NNP	Gender=Fem|Number=Sing	33	flat:name	_	SpaceAfter=No
35	,	_	PUNCT	,	_	36	punct	_	_
36	Asistente	_	NOUN	NN	Gender=Fem|Number=Sing	33	appos	_	_
37	Especial	_	ADJ	JJ	Gender=Fem|Number=Sing	36	amod	_	_
38	de	de	ADP	INDT	_	40	case	_	_
39	el	el	DET	_	Definite=Def|Gender=Masc|Number=Sing|PronType=Art	40	det	_	_
40	presidente	_	NOUN	NN	Gender=Masc|Number=Sing	36	nmod	_	_
41	Obama	_	PROPN	NNP	Gender=Masc|Number=Sing	40	appos	_	SpaceAfter=No
42	.	_	PUNCT	.	_	23	punct	_	_"""

In [34]:
true_labels = [line.split("\t")[3] for line in pos_example.split("\n")]
tokens = [line.split("\t")[1] for line in pos_example.split("\n")]

In [37]:
ids = tokenizer.subword_tokenize(tokens, true_labels)[0]
ids = tokenizer.convert_tokens_to_ids(ids)
mask = [1] * len(ids)
types = [0] * len(ids)
i = -1
result = {"tokens": [], "predicted_labels": [], "true_labels": []}
print("{:<25}{:<20}{:<20}".format("Token", "Predicted label", "True label"), "\n")
for token, label in zip(ids, model({"input_ids": tf.constant([ids]),
                                    "attention_mask": tf.constant([mask]),
                                    "token_type_ids": tf.constant([types])})[0].numpy().argmax(axis=-1)[0]):
    decoded_token = tokenizer.decode(token)
    if not decoded_token.startswith("# #") or decoded_token[-1] in [",", "."]:
        i += 1
    result["tokens"].append(decoded_token)
    result["predicted_labels"].append(tagset[label])
    result["true_labels"].append(true_labels[i])
    if tagset[label] == true_labels[i]:
        print("{:<25}{:<20}{:<20}".format(decoded_token, tagset[label], true_labels[i]))
    else:
        print("\x1b[31m{:<25}{:<20}{:<20}\x1b[0m".format(decoded_token, tagset[label], true_labels[i]))
print("\nAccuracy:", str(np.mean(np.array(result["predicted_labels"]) == np.array(result["true_labels"])) * 100)[:5] + "%")

Token                    Predicted label     True label           

A u n q u e              SCONJ               ADP                 
n o                      PART                ADV                 
h a y a                  VERB                VERB                
p r e c e d e n t e      NOUN                NOUN                
# # s                    NOUN                NOUN                
p a r a                  ADP                 ADP                 
l a                      DET                 DET                 
m a y o r                ADJ                 ADJ                 
p a r t e                NOUN                NOUN                
d e                      ADP                 ADP                 
l a                      DET                 DET                 
t r a n s i c i ó n      NOUN                NOUN                
d i g i t a l            ADJ                 ADJ                 
e n                      ADP                 ADP                 
E s t a 

In [207]:
((len(result["tokens"]) * 0.88) + (512 - len(result["tokens"]))) / 512

0.98828125

In [184]:
test_sentences = pyconll.load_from_file("../es_pud-ud-test.conllu")
test_dataset = convert_examples_to_tf_dataset(examples=test_sentences, tokenizer=tokenizer, tagset=tagset, max_length=512)
test_dataset = test_dataset.batch(32).repeat(1)
model.evaluate(test_dataset)[1]

1/1 [==============================] - 0s 7ms/step - loss: 0.0866 - accuracy: 0.9883


0.98828125

In [174]:
tokenizer.decode(test_dataset.as_numpy_iterator().next()[0]["input_ids"][0, :60])

'Aunque no haya precedentes para la mayor parte de la transición digital en Estados Unidos, la transición de poder pacífica es habitual, escribió el lunes en una entrada de blog Kori Schulman, Asistente Especial de el presidente Obama. [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD]'

In [182]:
np.array([tagset[index] for index in test_dataset.as_numpy_iterator().next()[1][0, :50]]) == np.array(result["true_labels"])

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True])

In [41]:
def read_conll(input_file):
        """Reads a conllu file."""
        ids = []
        texts = []
        tags = []
        #
        text = []
        tag = []
        for line in open(input_file, encoding="utf-8"):
            if line.startswith("# sent_id ="):
                idx = line.strip().split()[-1]
                ids.append(idx)
            elif line.startswith("#"):
                pass
            elif line.strip() == "":
                texts.append(text)
                tags.append(tag)
                text, tag = [], []
            else:
                try:
                    splits = line.strip().split()
                    token = splits[1] # the token
                    label = splits[3] # the UD POS Tag label
                    text.append(token)
                    tag.append(label)
                except ValueError:
                    print(idx)
        return ids, texts, tags

In [42]:
ids, texts, tags = read_conll(glob.glob("../data/ud/fi" + "/*-test.conllu")[0])

In [45]:
(np.array(ids) == "n01112014").argmax()

277

In [159]:
print(tags[277])

NameError: name 'tags' is not defined

In [160]:
print(texts[277])

NameError: name 'texts' is not defined

In [32]:
(np.array(labels) == None).argmax()

16

In [34]:
tokens[16]

'ellei'

In [32]:
path = "../data/ud/"
batch_size = 32
pos_eval = {}
for directory in tqdm(os.listdir(path)):
    lang_path = os.path.join(path, directory)
#     pos = open(glob.glob(lang_path + "/*-test.conllu")[0], "r", encoding="utf-8").read()
#     test_sentences = parse(pos)
    test_sentences = pyconll.load_from_file(glob.glob(lang_path + "/*-test.conllu")[0])
    test_dataset = convert_examples_to_tf_dataset(examples=test_sentences, tokenizer=tokenizer, tagset=tagset, max_length=512)
    test_dataset = test_dataset.shuffle(10000).batch(batch_size).repeat(1)
    pos_eval[directory] = model.evaluate(test_dataset)[1]

KeyError: 'tokens'

In [11]:
test_sentences = pyconll.load_from_file(glob.glob("../data/ud/zh" + "/*-test.conllu")[0])
test_dataset = convert_examples_to_tf_dataset(examples=test_sentences, tokenizer=tokenizer, tagset=tagset, max_length=512)
test_dataset = test_dataset.batch(32).repeat(1)
#model.evaluate(test_dataset)[1]

In [132]:
print([tokenizer.decode(int(token)) for token in test_dataset.as_numpy_iterator().next()[0]["input_ids"][0][:70]])

['"', '雖', '# # 然', '美', '# # 國', '的', '許', '# # 多', '數', '# # 字', '# # 化', '轉', '# # 型', '都', '# # 是', '史', '# # 無', '# # 前', '# # 例', '的', '，', '但', '權', '# # 力', '的', '和', '# # 平', '轉', '# # 移', '卻', '存', '# # 在', '先', '# # 例', '，', '[ U N K ]', '奧', '# # 巴', '# # 馬', '的', '特', '# # 別', '助', '# # 理', '科', '# # 瑞', '·', '舒', '# # 爾', '# # 曼', '在', '周', '一', '發', '# # 布', '的', '博', '# # 客', '中', '寫', '# # 道', '。', '[ P A D ]', '[ P A D ]', '[ P A D ]', '[ P A D ]', '[ P A D ]', '[ P A D ]', '[ P A D ]', '[ P A D ]']


In [18]:
print(tokenizer.subword_tokenize([token.form for token in test_sentences[0]], [3]*100))

(['"', '雖', '##然', '美', '##國', '的', '許', '##多', '數', '##字', '##化', '轉', '##型', '都', '##是', '史', '##無', '##前', '##例', '的', '，', '但', '權', '##力', '的', '和', '##平', '轉', '##移', '卻', '存', '##在', '先', '##例', '，', '[UNK]', '奧', '##巴', '##馬', '的', '特', '##別', '助', '##理', '科', '##瑞', '·', '舒', '##爾', '##曼', '在', '周', '一', '發', '##布', '的', '博', '##客', '中', '寫', '##道', '。'], [3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3], [0, 1, 1, 2, 2, 3, 4, 4, 5, 5, 5, 6, 6, 7, 7, 8, 8, 8, 8, 9, 10, 11, 12, 12, 13, 14, 14, 15, 15, 16, 17, 17, 18, 18, 19, 20, 21, 21, 21, 22, 23, 23, 24, 24, 25, 25, 26, 27, 27, 27, 28, 29, 30, 31, 31, 32, 33, 33, 34, 35, 35, 36])


In [19]:
print(tokenizer.convert_tokens_to_ids(tokenizer.subword_tokenize([token.form for token in test_sentences[0]], [3]*100)[0]))

[107, 8282, 115088, 6417, 112786, 5718, 7185, 112957, 4310, 113120, 112415, 7632, 112835, 7838, 114146, 2759, 115084, 112334, 112046, 5718, 10064, 2243, 4769, 112360, 5718, 2833, 113407, 7632, 115731, 2702, 3355, 112797, 2431, 112046, 10064, 100, 3229, 113360, 118276, 5718, 5410, 112316, 2602, 115281, 5954, 115314, 217, 6639, 115159, 114220, 3031, 2822, 2072, 5714, 113367, 5718, 2684, 113162, 2104, 3435, 117527, 1882]


In [24]:
print([tokenizer.decode(token) for token in tokenizer.convert_tokens_to_ids(tokenizer.subword_tokenize([token.form for token in test_sentences[0]], [3]*100)[0])])

['"', '雖', '# # 然', '美', '# # 國', '的', '許', '# # 多', '數', '# # 字', '# # 化', '轉', '# # 型', '都', '# # 是', '史', '# # 無', '# # 前', '# # 例', '的', '，', '但', '權', '# # 力', '的', '和', '# # 平', '轉', '# # 移', '卻', '存', '# # 在', '先', '# # 例', '，', '[ U N K ]', '奧', '# # 巴', '# # 馬', '的', '特', '# # 別', '助', '# # 理', '科', '# # 瑞', '·', '舒', '# # 爾', '# # 曼', '在', '周', '一', '發', '# # 布', '的', '博', '# # 客', '中', '寫', '# # 道', '。']


In [14]:
tokenizer.decode(int(test_dataset.as_numpy_iterator().next()[0]["input_ids"][0][:70][2]))

'# # 然'

In [134]:
tokenizer.decode(test_dataset.as_numpy_iterator().next()[0]["input_ids"][0][:70])

'" 雖然 美國 的 許多 數字化 轉型 都是 史無前例 的 ， 但 權力 的 和平 轉移 卻 存在 先例 ， [UNK] 奧巴馬 的 特別 助理 科瑞 · 舒爾曼 在 周 一 發布 的 博客 中 寫道 。 [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD]'

In [31]:
true_labels = [token.upos for token in test_sentences[0]]
tokens, true_labels, _ = tokenizer.subword_tokenize([token.form for token in test_sentences[0]], true_labels)
ids = tokenizer.convert_tokens_to_ids(tokens)

result = {"tokens": [], "predicted_labels": [], "true_labels": []}

print("{:<25}{:<20}{:<20}".format("Token", "Predicted label", "True label"), "\n")
for token, label, true_label in zip(ids, model(tf.constant([ids]))[0].numpy().argmax(axis=-1)[0], true_labels):
    decoded_token = tokenizer.decode(token)
    result["tokens"].append(decoded_token)
    result["predicted_labels"].append(tagset[label])
    result["true_labels"].append(true_label)
    if tagset[label] == true_label:
        print("{:<25}{:<20}{:<20}".format(decoded_token, tagset[label], true_label))
    else:
        print("\x1b[31m{:<25}{:<20}{:<20}\x1b[0m".format(decoded_token, tagset[label], true_label))
print("\nAccuracy:", str(np.mean(np.array(result["predicted_labels"]) == np.array(result["true_labels"])) * 100)[:5] + "%")

Token                    Predicted label     True label           

"                        PUNCT               PUNCT               
雖                        INTJ                SCONJ               
# # 然                    PART                SCONJ               
美                        PROPN               PROPN               
# # 國                    PROPN               PROPN               
的                        PART                PART                
許                        NOUN                NUM                 
# # 多                    NUM                 NUM                 
數                        NOUN                NOUN                
# # 字                    NOUN                NOUN                
# # 化                    NOUN                NOUN                
轉                        NOUN                NOUN                
# # 型                    NOUN                NOUN                
都                        AUX                 VERB                
# # 是   

In [28]:
path = os.path.join("../data/ud/", "fi")
test_data = read_conll("../data/ud/fi/fi_pud-ud-test.conllu")
index = np.where(np.array(test_data[0]) == "n01112014")[0][0]
tokens = test_data[1][index]
true_labels = test_data[2][index]
ids = tokenizer.subword_tokenize(tokens, true_labels)[0]
ids = tokenizer.convert_tokens_to_ids(ids)
mask = [1] * len(ids)
types = [0] * len(ids)
i = -1
result = {"tokens": [], "predicted_labels": [], "true_labels": []}
print("{:<25}{:<20}{:<20}".format("Token", "Predicted label", "True label"), "\n")
for token, label in zip(ids, model({"input_ids": tf.constant([ids]),
                                    "attention_mask": tf.constant([mask]),
                                    "token_type_ids": tf.constant([types])})[0].numpy().argmax(axis=-1)[0]):
    decoded_token = tokenizer.decode(token)
    if not decoded_token.startswith("# #") or decoded_token[-1] in [",", "."]:
        i += 1
    result["tokens"].append(decoded_token)
    result["predicted_labels"].append(tagset[label])
    result["true_labels"].append(true_labels[i])
    if tagset[label] == true_labels[i]:
        print("{:<25}{:<20}{:<20}".format(decoded_token, tagset[label], true_labels[i]))
    else:
        print("\x1b[31m{:<25}{:<20}{:<20}\x1b[0m".format(decoded_token, tagset[label], true_labels[i]))
print("\nAccuracy:", str(np.mean(np.array(result["predicted_labels"]) == np.array(result["true_labels"])) * 100)[:5] + "%")

Token                    Predicted label     True label           

T a m                    ADJ                 ADJ                 
# # m i k                ADJ                 ADJ                 
# # u u                  ADJ                 ADJ                 
# # l l i s              ADJ                 ADJ                 
# # e s s a              ADJ                 ADJ                 
t                        ADJ                 ADJ                 
# # ä r k e              ADJ                 ADJ                 
# # ä s s ä              ADJ                 ADJ                 
s e l v                  NOUN                NOUN                
# # i t y                NOUN                NOUN                
# # k s e s              NOUN                NOUN                
# # s ä                  PRON                NOUN                
t o                      VERB                VERB                
# # d e t t i i n        VERB                VERB                
,       